In [1]:
# %pip install gputil
# %pip install setuptools
# %pip install transformers
# %pip install torch

# %pip install auto-gptq #==0.4.0

What happens when you reflect or invert the input and output embeddings?

In [2]:
import GPUtil

from transformers import AutoModelForCausalLM, AutoTokenizer, pipeline
import torch
# from auto_gptq import AutoGPTQForCausalLM

/home/mick/pycharmprojects/Frankenstein/.venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
def grab_model(model_name, quantized = False):
    if quantized:
        model = AutoGPTQForCausalLM.from_quantized(model_name, device="cpu", use_safetensors=True)
    else:
        model = AutoModelForCausalLM.from_pretrained(model_name)

    tokenizer = AutoTokenizer.from_pretrained(model_name)
    return model, tokenizer

In [4]:
modelA, tokenizerA = grab_model("gpt2")
modelB, tokenizerB = grab_model("EleutherAI/gpt-neo-125M")

# modelA, tokenizerA = grab_model("EleutherAI/gpt-neo-125M-4bit", quantized=True)
# modelB, tokenizerB = grab_model("iproskurina/opt-125m-GPTQ-4bit-g128", quantized=True)

In [5]:
modelA.config.hidden_size == modelB.config.hidden_size 

True

In [6]:
emb1 = modelA.get_input_embeddings().weight
emb2 = modelB.get_input_embeddings().weight

In [7]:

# flip the matrix
emb1_R = emb1.flip(dims=[0]) # .reverse() #[::-1]

print("ModelA mean norms:", torch.norm(emb1, dim=1).mean().item())
print("Rotated modelA mean norms:", torch.norm(emb1_R, dim=1).mean().item())

new_embedding = torch.nn.Embedding.from_pretrained(emb1_R)

print("new_embedding mean norms:", torch.norm(new_embedding.weight, dim=1).mean().item())

modelA.set_input_embeddings(new_embedding)
modelA.lm_head.weight = new_embedding.weight


ModelA mean norms: 3.9585366249084473
Rotated modelA mean norms: 3.958536148071289
new_embedding mean norms: 3.958536148071289


In [8]:
modelA.lm_head.out_features == tokenizerA.vocab_size

True

In [9]:
# use model
pipe = pipeline("text-generation", model=modelA, tokenizer=tokenizerB)
print(pipe("Hello, how are you?"))

Device set to use cpu
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


[{'generated_text': 'Hello, how are you? tutor harsher Babe lobe composure OPEC PLUS partying composure 1886 harsher Christy ChristyJs typew composure PLUScapitalist youbush passively BinaryUGH HitmanMachPatch annihilation composure hauled invoking totem MILL954 Rated pavement Mercenary methodological harsher Christy Christyanskyighting Cantor composureintensityscrollcapitalistMach Akron Brilliant Mercenary Innocent HitmanOIL typew briefingsMachTranslation Berkshire composureishy harsher Canary harsherEnhanced harsher Hoyishy harsher Canary harsherAlternative SpoMachatakacapitalist Salon chemicallyMethods annihilation Vortex unrem Hitman chemicallychev typewzie annihilation composureishy harsher Canary harsher annihilation pige harsher Christy Christyaimon composure Dartmouth reef Hitman composureishy harsher Canary harsherEnhancedAlternativeflame TECH annihilationuntarilytera Codeslations composure arra Bicycle harsher Christy Christyanskyishy harsher Canary harsherEnhanced typewWhere